In [ ]:
import sys
print(sys.version)
import numpy as np
import matplotlib.pyplot as plt
import plotly as plotly
import plotly.graph_objects as go
import plotly.io as pio
from IPython.display import Image, display
from mined_metric.jupyter.utils.data_access_util import get_validation_data
from mined_metric.jupyter.utils.prediction_util import filter_exp_data
import operator

In [ ]:
# Data loading
VALIDATION_ID = "VALIDATION_ID_PLACEHOLDER"

exp_datas = {}

for data in get_validation_data(VALIDATION_ID):
    if "exception" in data:
        print("Invalid data is returned: {}".format(data["exception"]))
    key = data["experiment"]["additionalMsg"] or data["experiment"]["id"]
    exp_datas[key] = data
filter_exp_data(exp_datas)


In [ ]:
class ScoresLabels:
    def __init__(self, score, label):
        self.score = score
        self.label = label
        
class PrecisionRecallPoint:
    def __init__(self, precision, recall, score, num_results):
        self.precision = precision
        self.recall = recall
        self.score = score
        self.num_results = num_results
    
def calculatePRPoints(samples):
    scores = []
    labels = []
    for sample in samples:
        if 'classification_result' in sample:
            score = sample['classification_result']['score']
            if isinstance(score, str):
                continue
            scores.append(score)
            labels.append(sample['classification_result']['label'])
    scores_labels_list = []
    npos = 0
    for idx, val in enumerate(scores):
        scores_labels_list.append(ScoresLabels(scores[idx], labels[idx]))
        if labels[idx]:
            npos += 1
    
    if npos == 0:
        return []
    
    scores_labels_list.sort(key=operator.attrgetter('score'), reverse=True)
    
    tp = 0
    fp = 0
    pr_points = []
    for score_label in scores_labels_list:
        if score_label.label:
            tp += 1
        else:
            fp += 1
        if len(pr_points) == 0 or score_label.score != pr_points[-1].score:
            pr_points.append(PrecisionRecallPoint(tp / float(tp + fp), tp / float(npos), score_label.score, tp + fp))
            
    return pr_points

def histogram(x_input, n_bins, bin_size, max_val=1):
    x_input.sort()
    bins = []
    for i in range(-1, n_bins + 1):
        bins.append(float(i) / bin_size)
        
    hist = [0.0 for _ in range(n_bins + 1)]

    x_ind = 0
    bin_ind = 0
    while x_ind < len(x_input) and bin_ind < len(bins):
        if x_input[x_ind] < bins[0]:
            x_ind += 1
        elif x_input[x_ind] <= bins[bin_ind]:
            hist[bin_ind - 1] += 1
            x_ind += 1
        else:
            bin_ind += 1

    for i in range(0, n_bins + 1):
        hist[i] = float(hist[i]) / len(x_input)

    for i in range(1, n_bins + 1):
        hist[i] = hist[i] + hist[i-1]
        
    for i in range(0, n_bins + 1):
        hist[i] *= max_val
    
    return hist, bins

def populate_flicker_histogram(figure, flicker_hist, bins, experiment_id):
    dtype = [('flicker_rate', float), ('flicker_fraction', float)]
    points = np.empty(len(flicker_hist), dtype=dtype)
    for i, hist_val in enumerate(flicker_hist):
        points[i] = (flicker_hist[i], bins[i + 1])

    np.sort(points, order=['flicker_fraction'])
    figure = figure.add_trace(go.Scatter(
        name = experiment_id,
        x=points['flicker_fraction'], 
        y=points['flicker_rate']
    ))
    return figure

def make_figure(title, xaxis_title, yaxis_title):
    fig = go.Figure()
    fig.update_layout(
        title=title,
        xaxis_title=xaxis_title,
        yaxis_title=yaxis_title
    )
    fig.update_layout(
        autosize=False,
        width=800,
        height=600,
    )
    return fig

def print_event_count(experiment_id, event_type_name, event_count):
    print(f'Num {event_type_name} in experiment {experiment_id}: {event_count}')

clf_samples = {}
reg_samples = {}

for experiment_id, data in exp_datas.items():
    clf_samples[experiment_id] = []
    reg_samples[experiment_id] = []
    for d in data["meta"]:
        if 'result' not in d:
            continue
        result = d['result']
        if 'sample' in result:
            for sample in result['sample']:
                if 'classification_result' in sample and sample['classification_result']:
                    clf_samples[experiment_id].append(sample)
                if 'regression_result' in sample and sample['regression_result']:
                    reg_samples[experiment_id].append(sample)
                    
tags = ['All Samples', 'Non-TL Junction', 'TL Junction']

for tag in tags:
    print('Tag: %s' % tag)
    print("Classification Metrics")
    pr_curve_fig = make_figure('Precision-Recall Curve',
                               'Recall',
                               'Precision')

    for experiment_id, samples in clf_samples.items():
        samples_with_tag = []
        for sample in samples:
            if tag ==  'All Samples' or tag in sample['tags']:
                samples_with_tag.append(sample)
        total_samples = len(samples_with_tag)
        pr_points = calculatePRPoints(samples_with_tag)
        print('Number of samples in experiemnt {}: {}'.format(experiment_id, total_samples))
        dtype = [('precision', float), ('recall', float), ('score', float), ('num_results', int)]
        points = np.empty(len(pr_points), dtype=dtype)
        for i, pr_point in enumerate(pr_points):
            points[i] = (pr_point.precision, pr_point.recall, pr_point.score, pr_point.num_results)
            
        np.sort(points, order=['recall'])
        pr_curve_fig = pr_curve_fig.add_trace(go.Scatter(
            name = experiment_id,
            x=points['recall'], 
            y=points['precision']
        ))
    pr_curve_fig.show()
    
    positive_flicker_fig = make_figure('Positive Flicker Rate',
                                       'Flicker Fraction',
                                       'Cumulative Histogram')
    negative_flicker_before_fig = make_figure('Negative Flicker Rate Before',
                                              'Flicker Fraction',
                                              'Cumulative Histogram')
    negative_flicker_after_fig = make_figure('Negative Flicker Rate After',
                                             'Flicker Fraction',
                                             'Cumulative Histogram')
    time_to_predict_fig = make_figure('Time to Predict',
                                      'Time (s)',
                                      'Cumulative Histogram')
    time_to_predict_negative_after_fig = make_figure('Time to Predict Negative After',
                                                     'Time (s)',
                                                     'Cumulative Histogram')
    
    for experiment_id, data in exp_datas.items():
        negative_flicker_rate_before = []
        positive_flicker_rate = []
        negative_flicker_rate_after = []
        times_to_predict = []
        times_to_predict_negative_after = []
        for d in data['meta']:
            if 'negative_flicker_rate_before' in d:
                negative_flicker_rate_before.append(d['negative_flicker_rate_before'])
            if 'positive_flicker_rate' in d:
                positive_flicker_rate.append(d['positive_flicker_rate'])
            if 'negative_flicker_rate_after' in d:
                negative_flicker_rate_after.append(d['negative_flicker_rate_after'])
            if 'time_to_predict' in d:
                time_to_predict = d['time_to_predict']
                if isinstance(time_to_predict, str):
                    time_to_predict = 10000
                times_to_predict.append(time_to_predict)
            if 'time_to_predict_negative_after' in d:
                time_to_predict = d['time_to_predict_negative_after']
                if isinstance(time_to_predict, str):
                    time_to_predict = 10000
                times_to_predict_negative_after.append(time_to_predict)
        
        print_event_count(experiment_id, 'positive events', len(positive_flicker_rate))
        print_event_count(experiment_id, 'negative before events', len(negative_flicker_rate_before))
        print_event_count(experiment_id, 'negative after events', len(negative_flicker_rate_after))
        negative_flicker_before_hist, negative_flicker_before_bins = histogram(negative_flicker_rate_before, 100, 100)
        negative_flicker_after_hist, negative_flicker_after_bins = histogram(negative_flicker_rate_after, 100, 100)
        positive_flicker_hist, positive_flicker_bins = histogram(positive_flicker_rate, 100, 100)
        time_to_predict_hist, time_to_predict_bins = histogram(times_to_predict, 100, 10)
        time_to_predict_negative_after_hist, time_to_predict_negative_after_bins = histogram(
            times_to_predict_negative_after, 100, 10)

        positive_flicker_fig = populate_flicker_histogram(positive_flicker_fig,
                                                          positive_flicker_hist,
                                                          positive_flicker_bins,
                                                          experiment_id)
        negative_flicker_before_fig = populate_flicker_histogram(negative_flicker_before_fig,
                                                                 negative_flicker_before_hist,
                                                                 negative_flicker_before_bins,
                                                                 experiment_id)
        negative_flicker_after_fig = populate_flicker_histogram(negative_flicker_after_fig,
                                                                negative_flicker_after_hist,
                                                                negative_flicker_after_bins,
                                                                experiment_id)
        time_to_predict_fig = populate_flicker_histogram(time_to_predict_fig,
                                                         time_to_predict_hist,
                                                         time_to_predict_bins,
                                                         experiment_id)
        time_to_predict_negative_after_fig = populate_flicker_histogram(time_to_predict_negative_after_fig,
                                                                        time_to_predict_negative_after_hist,
                                                                        time_to_predict_negative_after_bins,
                                                                        experiment_id)
        
    positive_flicker_fig.show()
    negative_flicker_before_fig.show()
    negative_flicker_after_fig.show()
    time_to_predict_fig.show()
    time_to_predict_negative_after_fig.show()
    
    print("Regression Metrics")
    s_offset_error_under_fig = make_figure("S-Offset Error (Underestimate)",
                                     "Distance (m)",
                                     "Cumulative Histogram")
    s_offset_error_over_fig = make_figure("S-Offset Error (Overestimate)",
                                     "Distance (m)",
                                     "Cumulative Histogram")
    l2_offset_error_fig = make_figure("l2 Error",
                                     "Distance (m)",
                                     "Cumulative Histogram")
    
    for experiment_id, samples in reg_samples.items():
        samples_with_tag = []
        s_errors_over = []
        s_errors_under = []
        l2_errors = []
        for sample in samples:
            if tag ==  'All Samples' or tag in sample['tags']:
                samples_with_tag.append(sample)
        for sample in samples_with_tag:    
            if sample['regression_result']['error_type'] == 'S_OFFSET':
                error = sample['regression_result']['error']
                if error > 0:
                    s_errors_over.append(error)
                else:
                    s_errors_under.append(abs(error))

            if sample['regression_result']['error_type'] == 'L2_DISTANCE':
                l2_errors.append(abs(sample['regression_result']['error']))
                
        total_s_over = len(s_errors_over)
        total_s_under = len(s_errors_under)
        total_s_errors = total_s_over + total_s_under
        total_s_over_pct = float(total_s_over) / total_s_errors
        total_s_under_pct = float(total_s_under) / total_s_errors
            
        s_errors_over_hist, s_errors_over_bins = histogram(s_errors_over, 100, 10, max_val=total_s_over_pct)
        s_errors_under_hist, s_errors_under_bins = histogram(s_errors_under, 100, 10, max_val=total_s_under_pct)
        l2_errors_hist, l2_errors_bins = histogram(l2_errors, 100, 10) 
        s_offset_error_over_fig = populate_flicker_histogram(s_offset_error_over_fig,
                                                             s_errors_over_hist,
                                                             s_errors_over_bins,
                                                             experiment_id)
        s_offset_error_under_fig = populate_flicker_histogram(s_offset_error_under_fig,
                                                              s_errors_under_hist,
                                                              s_errors_under_bins,
                                                              experiment_id)
        l2_offset_error_fig = populate_flicker_histogram(l2_offset_error_fig,
                                                         l2_errors_hist,
                                                         l2_errors_bins,
                                                         experiment_id)

    s_offset_error_over_fig.show()
    s_offset_error_under_fig.show()
    l2_offset_error_fig.show()